In [2]:
import os
import logging
from pymongo import MongoClient
import sys
import json
from bson import ObjectId
from datetime import datetime
from dotenv import load_dotenv

load_dotenv(os.path.join(os.getcwd(), '.env'), override=True)

MONGO_URI = os.getenv("MONGO_URI")
DB_NAME = os.getenv("DB_NAME")

class MongoEncoder(json.JSONEncoder):
    def default(self, obj):
        if isinstance(obj, ObjectId):
            return str(obj)
        if isinstance(obj, datetime):
            return obj.isoformat()
        return super().default(obj)

def connect_db():
    client = MongoClient(MONGO_URI)
    db = client[DB_NAME]
    return db

def print_json(q_name, result):
    data = []
    if isinstance(result, list):
        data = result
    else:
        for doc in result:
            data.append(doc)
            if len(data) >= 5: break
    
    print(json.dumps(data, cls=MongoEncoder, indent=4))

db = connect_db()

### Q1: Name and surname of players for a specific club.

In [3]:
club_name = "SV Darmstadt 98"

res = db.clubs.find({"name": club_name}, { "players.name": 1, "players.surname": 1, "_id": 0 })
print_json("Q1", res)

[
    {
        "players": [
            {
                "name": "Patrick",
                "surname": "Platins"
            },
            {
                "name": "Hamit",
                "surname": "Altintop"
            },
            {
                "name": "Gy\u00f6rgy",
                "surname": "Garics"
            },
            {
                "name": "Peter",
                "surname": "Niemeyer"
            },
            {
                "name": "Aytac",
                "surname": "Sulu"
            },
            {
                "name": "Michael",
                "surname": "Stegmayer"
            },
            {
                "name": "Markus",
                "surname": "Steinh\u00f6fer"
            },
            {
                "name": "Marco",
                "surname": "Sailer"
            },
            {
                "name": "Dominik",
                "surname": "Stroh-Engel"
            },
            {
                "name": "Milan",
         

### Q2: For every club the home stadium.

In [4]:
res = db.clubs.find( {}, { "name": 1, "stadium_name": 1, "_id": 0 } )
print_json("Q2", res)

[
    {
        "name": "SV Darmstadt 98",
        "stadium_name": "Merck-Stadion am B\u00f6llenfalltor"
    },
    {
        "name": "Ural Yekaterinburg",
        "stadium_name": "Yekaterinburg Arena"
    },
    {
        "name": "Be\u015fikta\u015f Jimnastik Kul\u00fcb\u00fc",
        "stadium_name": "Be\u015fikta\u015f Park"
    },
    {
        "name": "Associazione Sportiva Roma",
        "stadium_name": "Olimpico di Roma"
    },
    {
        "name": "Tottenham Hotspur Football Club",
        "stadium_name": "Tottenham Hotspur Stadium"
    }
]


### Q3: Given a club, the average valuation of players (for each player the most recent valuation).

In [ ]:
club_name = "Juventus Football Club"

pipeline_q3 = [
    { "$match": { "name": club_name } },
    { "$unwind": "$players" },
    { "$unwind": "$players.player_valuation" },
    { "$sort": { "players.player_valuation.date": -1 } },
    { "$group": { 
        "_id": { "name": "$players.name", "surname": "$players.surname" }, 
        "latest_value": { "$first": "$players.player_valuation.market_value" } 
    }},
    { "$group": { "_id": None, "average_valuation": { "$avg": "$latest_value" } } }
]
res = db.clubs.aggregate(pipeline_q3, allowDiskUse=True) # we need to add allowDiskUse because the default memory space provide by mongo is not enough to allow query exection
print_json("Q3", list(res))

[
    {
        "_id": null,
        "average_valuation": 7216173.469387755
    }
]


### Q4: For each country, players with citizenship.

In [6]:
pipeline_q4 = [
    { "$group": { 
        "_id": "$citizenship_country_name", 
        "list_of_players": { "$push": { "name": "$name", "surname": "$surname" } } 
    }}
]
res = db.players.aggregate(pipeline_q4)
print_json("Q4", list(res))

[
    {
        "_id": "Curacao",
        "list_of_players": [
            {
                "name": "Angelo",
                "surname": "Cijntje"
            },
            {
                "name": "Kemy",
                "surname": "Agustien"
            },
            {
                "name": "Vurnon",
                "surname": "Anita"
            },
            {
                "name": "Rihairo",
                "surname": "Meulens"
            },
            {
                "name": "Guyon",
                "surname": "Fernandez"
            },
            {
                "name": "Boy",
                "surname": "Deul"
            },
            {
                "name": "Charlison",
                "surname": "Benschop"
            },
            {
                "name": "Eloy",
                "surname": "Room"
            },
            {
                "name": "Romero",
                "surname": "Regales"
            },
            {
                "name": "Gianlu

### Q5: Given a role, information (name, surname and birthdate) of players who have played in at least one game in a certain competition.

In [16]:
player_role = "Attack"
comp_target = "L1"

res = db.players.find(
    { "position": player_role, "plays_in_competition": comp_target }, 
    { "name": 1, "surname": 1,  "birthdate": 1, "_id": 0 }
)
print_json("Q5", res)

[
    {
        "surname": "Asamoah",
        "name": "Gerald",
        "birthdate": "1978-10-03 00:00:00"
    },
    {
        "surname": "Pizarro",
        "name": "Claudio",
        "birthdate": "1978-10-03 00:00:00"
    },
    {
        "surname": "Klasnic",
        "name": "Ivan",
        "birthdate": "1980-01-29 00:00:00"
    },
    {
        "surname": "Voronin",
        "name": "Andriy",
        "birthdate": "1979-07-21 00:00:00"
    },
    {
        "surname": "Kuranyi",
        "name": "Kevin",
        "birthdate": "1982-03-02 00:00:00"
    }
]


### Q6: Games list, with home team date and stadium, for a certain competition in which the home team has scored more than N goals.

In [20]:
n_goals = 2
comp_target = "FR1"

res = db.games1.find(
   {"competition_id": comp_target, "home_club_goals": { "$gt": n_goals }}, 
   { "home_club_name": 1, "date": 1, "stadium_name": 1, "home_club_goals": 1, "_id": 0 }
)
print_json("Q6", res)

[
    {
        "home_club_goals": 3.0,
        "date": "2014-02-08",
        "home_club_name": "AC Ajaccio",
        "stadium_name": "Stade Fran\u00e7ois-Coty"
    },
    {
        "home_club_goals": 3.0,
        "date": "2014-11-23",
        "home_club_name": "Olympique de Marseille",
        "stadium_name": "Orange V\u00e9lodrome"
    },
    {
        "home_club_goals": 3.0,
        "date": "2015-09-12",
        "home_club_name": "FC Lorient",
        "stadium_name": "Stade du Moustoir"
    },
    {
        "home_club_goals": 3.0,
        "date": "2017-04-30",
        "home_club_name": "Olympique Gymnaste Club Nice C\u00f4te d'Azur",
        "stadium_name": "Allianz Riviera"
    },
    {
        "home_club_goals": 3.0,
        "date": "2017-09-23",
        "home_club_name": "Olympique Lyonnais",
        "stadium_name": "Groupama Stadium"
    }
]


### Q7: For a given referee, the average number of cards per game.

In [15]:
referee = "Cagatay Sahan"
game_events_type = "Cards"

pipeline_q7 = [
   { "$match": { "referee": referee } },
   { "$unwind": "$game_events" },
   { "$match": { "game_events": game_events_type } },
   { "$group": { "_id": "$game_id", "count_for_game": { "$sum": 1 } } },
   { "$group": { "_id": None, "average_cards": { "$avg": "$count_for_game" } } }
]
res = db.games2.aggregate(pipeline_q7)
print_json("Q7", list(res))

[
    {
        "_id": null,
        "average_cards": 4.956521739130435
    }
]


### Q8: List of stadiums where a particular club has played as the 'away' team.

In [10]:
club_name = "Juventus Football Club"

res = db.clubs.find( { "name": club_name }, { "away_stadium_name": 1, "_id": 0 } )
print_json("Q8", res)

[
    {
        "away_stadium_name": [
            "Dacia Arena",
            "Ali Sami Yen Spor Kompleksi RAMS Park",
            "Giuseppe Meazza",
            "Olimpico di Roma",
            "Comunale Renzo Barbera \"La Favorita\"",
            "Gewiss Stadium",
            "Bluenergy Stadium",
            "Luigi Ferraris",
            "Arechi",
            "Carlo Castellani",
            "Ram\u00f3n S\u00e1nchez-Pizju\u00e1n",
            "Ettore Giardiniero",
            "Olimpico Grande Torino",
            "Artemio Franchi",
            "Etihad Stadium",
            "Allianz Arena",
            "Stade Louis-II",
            "Marcantonio Bentegodi",
            "SIGNAL IDUNA PARK",
            "Stadio Diego Armando Maradona",
            "NSK Olimpisky",
            "Diego Armando Maradona",
            "Parken",
            "Unipol Domus",
            "Villa Park",
            "Mapei Stadium - Citt\u00e0 del Tricolore",
            "Ennio Tardini",
            "Est\u00e1dio do D

### Q9: List of stadiums used for matches in a specific competition.

In [11]:
comp_name = "serie-a"

res = db.competitions.find({"name": comp_name}, {"stadiums": 1, "_id": 0})
print_json("Q9", res)

[
    {
        "stadiums": [
            "Dacia Arena",
            "Artemio Franchi",
            "Giuseppe Meazza",
            "Marcantonio Bentegodi",
            "Luigi Ferraris",
            "Olimpico di Roma",
            "Comunale Renzo Barbera \"La Favorita\"",
            "Olimpico Grande Torino",
            "Sant'Elia",
            "Diego Armando Maradona",
            "Orogel Stadium - Dino Manuzzi",
            "Gewiss Stadium",
            "Comunale Matusa",
            "Allianz Stadium",
            "Ezio Scida",
            "Paolo Mazza",
            "Bluenergy Stadium",
            "Unipol Domus",
            "Stadio Diego Armando Maradona",
            "Nereo Rocco",
            "Ennio Tardini",
            "Mapei Stadium - Citt\u00e0 del Tricolore",
            "Carlo Castellani",
            "Pier Luigi Penzo",
            "Arechi",
            "Ettore Giardiniero",
            "Brianteo",
            "Benito Stirpe",
            "Stadio Olimpico Grande Torino",
 

### Q10: For each referee, the number of matches refereed.

In [12]:
pipeline_q10 = [
   { "$group": { "_id": "$referee", "number_of_matches": { "$sum": 1 } } }
]
res = db.games2.aggregate(pipeline_q10)
print_json("Q10", list(res))

[
    {
        "_id": "C\u00e9sar Ramos Palazuelos",
        "number_of_matches": 4
    },
    {
        "_id": "C\u00e9sar Soto Grado",
        "number_of_matches": 150
    },
    {
        "_id": "Sam Loeman",
        "number_of_matches": 19
    },
    {
        "_id": "Thijs Voncken",
        "number_of_matches": 5
    },
    {
        "_id": "Aaron Jackson",
        "number_of_matches": 3
    },
    {
        "_id": "Francesco Luciani",
        "number_of_matches": 1
    },
    {
        "_id": "Sarper Bar\u0131\u015f Saka",
        "number_of_matches": 44
    },
    {
        "_id": "Andrea Romeo",
        "number_of_matches": 19
    },
    {
        "_id": "Kristina Kozorog",
        "number_of_matches": 6
    },
    {
        "_id": "Aleksey Shishkin",
        "number_of_matches": 4
    },
    {
        "_id": "Mikhail Kazantsev",
        "number_of_matches": 2
    },
    {
        "_id": "Marios Lampropoulos",
        "number_of_matches": 45
    },
    {
        "_id": "Gerg\u

### Q11: Given a stadium, list all matches played in a specific season (date and teams).

In [13]:
stadium = "Allianz Stadium"
season = 2012

res = db.games1.find({ "stadium_name": stadium, "season": season }, 
   { "date": 1, "home_club_name": 1, "away_club_name": 1, "_id": 0 }
)
print_json("Q11", res)

[
    {
        "date": "2013-03-10",
        "home_club_name": "Juventus Football Club",
        "away_club_name": "Catania FC"
    },
    {
        "date": "2012-11-07",
        "home_club_name": "Juventus Football Club",
        "away_club_name": "Fodbold Club Nordsj\u00e6lland"
    },
    {
        "date": "2012-12-16",
        "home_club_name": "Juventus Football Club",
        "away_club_name": "Atalanta Bergamasca Calcio S.p.a."
    },
    {
        "date": "2012-10-02",
        "home_club_name": "Juventus Football Club",
        "away_club_name": "FC Shakhtar Donetsk"
    },
    {
        "date": "2013-02-09",
        "home_club_name": "Juventus Football Club",
        "away_club_name": "Associazione Calcio Fiorentina"
    }
]


### Q12: Given a player, show the complete history of his market valuations.

In [14]:
player_name = "Cristiano"
player_surname = "Del Grosso"
player_birthdate = "1983-03-24 00:00:00"

res = db.players.find(
    { "name": player_name, "surname": player_surname, "birthdate": player_birthdate}, 
    { "player_valuation": 1, "_id": 0 }
)
print_json("Q12", res)

[
    {
        "player_valuation": [
            {
                "market_value": 300000,
                "date": "2006-01-23"
            },
            {
                "market_value": 500000,
                "date": "2007-03-19"
            },
            {
                "market_value": 900000,
                "date": "2007-06-18"
            },
            {
                "market_value": 500000,
                "date": "2008-01-21"
            },
            {
                "market_value": 1000000,
                "date": "2009-02-02"
            },
            {
                "market_value": 1200000,
                "date": "2009-08-06"
            },
            {
                "market_value": 900000,
                "date": "2010-06-30"
            },
            {
                "market_value": 900000,
                "date": "2011-06-20"
            },
            {
                "market_value": 900000,
                "date": "2012-01-10"
            },
      